In [1]:
# Model design
import agentpy as ap

# Visualization
import matplotlib.pyplot as plt
import seaborn as sns
import IPython
import random

# List of robot available movements
MOVES = [(0, -1), (0, 1), (1, 0), (-1,0)]

In [19]:
class RoomModel(ap.Model):

    def setup(self):
        grid_size = self.p.M * self.p.N 
        dirty_tiles  = int( grid_size * self.p.dirtDensity)
        nRobots = int(self.p.nRobots)
        
        # Defining agents 
        self.robot = ap.AgentList(self,nRobots)
        self.dirty_tiles = ap.AgentList(self, dirty_tiles)

        # Defining room size
        self.room = ap.Grid(self, [self.p.M, self.p.N], track_empty=True)
        
        # Add agents to grid 
        self.room.add_agents(self.dirty_tiles, random=True, empty=True)
        self.room.add_agents(self.robot, [(1,1)] * nRobots)

        # Initiate a dynamic variable for all tiles
        # agent_type =  0: robot, 1: Dirty, 2: Cleaned
        self.robot.agent_type = 0
        self.dirty_tiles.agent_type = 1 

    def step(self):
        robots = self.robot
        
        # Robot behavior
        for robot in robots:
            for neighbor in self.room.neighbors(robot):
                if neighbor.agent_type == 1:
                    neighbor.agent_type = 2
                    break
            else:
                self.room.move_by(robot, random.choice(MOVES))
            
        # Stop simulation if no dirty tiles left
        tiles_to_clean = self.dirty_tiles.select(self.dirty_tiles.agent_type == 1)
        if len(tiles_to_clean) ==  0:
            self.stop()

    def end(self):
        # Document a measure at the end of the simulation
        cleaned_tiles = len(self.dirty_tiles.select(self.dirty_tiles.condition == 2))
        self.report('Percentage of cleaned tiles', cleaned_tiles / len(self.dirty_tiles))
        print(self.report['Percentage of cleaned tiles'])

In [33]:
# Define parameters

parameters = {
    'nRobots': 6, # Number of cleaning robot agents
    'dirtDensity': .8, # Percentage of dirty tile in the room
    'M': 25, # Height of the room
    'N': 35, # Lenght of the room
    'steps': 300 # Number of simulation steps
}

In [34]:
# Create single-run animation with custom colors

def animation_plot(model, ax):
    grid_size = parameters["M"]* parameters["N"]
    initial_dirty_tiles = parameters["dirtDensity"] * grid_size
    
    cleaned_tiles = len(model.dirty_tiles.select(model.dirty_tiles.agent_type == 2))
    cleaning_percentage = float("{:.2f}".format( cleaned_tiles / (initial_dirty_tiles) * 100))
    dirty_tiles = len(model.dirty_tiles.select(model.dirty_tiles.agent_type == 1))

    attr_grid = model.room.attr_grid('agent_type')
    color_dict = {0:'#96D7FF', 1:'#d2c1ad', 2:'#FFFFFF', None:'#FFF'}
    ap.gridplot(attr_grid, ax=ax, color_dict=color_dict, convert=True)
    ax.set_title(f"Simulation of a Robot cleaning a Room\n"
                 f"Time-step: {model.t} "f"Dirty tiles left: {dirty_tiles} "f"Cleaning porcentage: { cleaning_percentage }%",
                 color="white") 

fig, ax = plt.subplots()
model = RoomModel(parameters)
animation = ap.animate(model, fig, ax, animation_plot)
IPython.display.HTML(animation.to_jshtml(fps=15))